In [1]:
import librosa
import statistics
import librosa.display
import numpy as np
import binascii
import matplotlib.pyplot as plt
from PIL import Image
from IPython import display
import scipy.signal as signal
from sklearn import svm
from sklearn import ensemble
from sklearn import neural_network
import cv2
import csv
import os
import json

In [46]:
data, rate = librosa.load('data/videos/20.mp4', sr=None)
display.Audio(data, rate=rate)

In [47]:
data = data[12000:-12000]

In [2]:
f, t, z = signal.spectrogram(data, rate)
plt.pcolormesh(t, f, z)
plt.ylabel('Frequency [Hz]')
plt.ylim([0,2500])
plt.tight_layout()
plt.xlabel('Time [sec]')
plt.show()

NameError: name 'data' is not defined

In [ ]:
f, t, z = signal.stft(data, fs=48000, window='hann', noverlap = 900, nperseg=1200, return_onesided=True)
print(z.shape)
z = np.abs(z)
frequencies = []
sum_vals = []
zero_indices = []
for idx in range(int(len(t)/4)):
    window_basis = z[:, 4*idx] + z[:, 4*idx + 1] + z[:, 4*idx + 2] + z[:, 4*idx + 3]
    frequencies.append(f[np.argmax(window_basis)])
    sum_vals.append(np.sum(window_basis))
    if np.sum(window_basis) < 0.25:
        zero_indices.append(idx)
    
z = z.T
plt.plot(sum_vals)
print(zero_indices)

In [13]:
data, rate = librosa.load('videos/1.mp4', sr=None)
display.Audio(data, rate=rate)

In [5]:
def extract_key_strokes(file_name, threshold=0.026, nperseg=1200, noverlap=900):
    data, rate = librosa.load(file_name, sr=None)
    # remove first and last bit:
    
    data = data[12000:-12000]

    f, t, z = signal.stft(data, fs=rate, window='hamming', noverlap = noverlap, nperseg=nperseg, return_onesided=True)
    z = np.abs(z)
    frequencies = []
    sum_vals = []
    hits = []
    prev = -1
    for idx in range(int(len(t)/4)):
        window_basis = z[:, 4*idx] + z[:, 4*idx + 1] + z[:, 4*idx + 2] + z[:, 4*idx + 3]
        frequencies.append(f[np.argmax(window_basis)])
        sum_vals.append(np.sum(window_basis))
        if np.sum(window_basis) > threshold:
            if prev == -1:
                prev = idx
        else:
            if prev > -1:
                hits.append((idx + prev + 2) / 2 )
            prev = -1
    if prev > -1:
        hits.append((len(t) + prev + 2) / 2 )

    z = z.T
    #plt.plot(sum_vals)
                     
    hits = np.array(hits)
    hits = ((hits * nperseg) + 12000) / rate
    #print(len(hits))
    return hits

In [100]:
test_1 = extract_key_strokes('videos/0.mp4', 0.026, nperseg=1200, noverlap=900)
test_2 = extract_key_strokes('videos/1.mp4', 0.026, nperseg=1200, noverlap=900)
test_3 = extract_key_strokes('videos/2.mp4', 0.026, nperseg=1200, noverlap=900)

14
17
8


In [27]:
print(test_1)

[1.7125 2.     2.2125 2.475  2.6875 2.925  3.175  3.8125 4.3875 4.6
 4.7875 5.0375 5.3625 5.6125]


In [6]:
word_list = []
with open('data/word_list.csv') as csv_file:
    csv_reader = csv.reader(csv_file, delimiter=',')
    line_count = 0
    for row in csv_reader:
        word_list.append(row[0])
        
word_list = word_list[:100]

In [7]:
key_mappings = []
for i in range(len(word_list)):
    video_source = 'data/videos/{}.mp4'.format(i)
    #assert len(test[i]) == len(word_list[i])
    time_frames = extract_key_strokes(video_source, 0.016, nperseg=1200, noverlap=900) #original: 0.026
    
    if len(time_frames) == len(word_list[i]):
        print("MATCHED!")
        key_mappings.append((video_source, time_frames, word_list[i]))
    else:
        print((len(time_frames), len(word_list[i])))
    
print(len(key_mappings))

MATCHED!
MATCHED!
MATCHED!
(44, 32)
(20, 17)
(12, 11)
(22, 15)
(36, 28)
(10, 9)
(21, 13)
MATCHED!
(16, 15)
(19, 14)
(13, 11)
(13, 11)
(17, 12)
(37, 32)
(11, 10)
(45, 35)
(32, 24)
(53, 43)
MATCHED!
(33, 32)
(18, 16)
MATCHED!
MATCHED!
(19, 20)
MATCHED!
(10, 11)
MATCHED!
(26, 24)
MATCHED!
MATCHED!
(19, 21)
(39, 43)
(27, 28)
(19, 20)
MATCHED!
MATCHED!
(12, 14)
(23, 26)
(13, 12)
(29, 27)
MATCHED!
(18, 17)
MATCHED!
(13, 12)
MATCHED!
MATCHED!
(28, 31)
MATCHED!
MATCHED!
MATCHED!
(12, 13)
(35, 36)
MATCHED!
MATCHED!
MATCHED!
(14, 13)
MATCHED!
MATCHED!
MATCHED!
MATCHED!
(10, 9)
MATCHED!
MATCHED!
MATCHED!
MATCHED!
MATCHED!
MATCHED!
(22, 16)
MATCHED!
MATCHED!
(16, 15)
MATCHED!
MATCHED!
(24, 25)
MATCHED!
MATCHED!
MATCHED!
(13, 12)
MATCHED!
(8, 9)
MATCHED!
MATCHED!
(23, 24)
MATCHED!
MATCHED!
MATCHED!
MATCHED!
(19, 18)
MATCHED!
MATCHED!
(11, 12)
(15, 14)
MATCHED!
MATCHED!
MATCHED!
MATCHED!
(31, 32)
53


In [39]:
print(len(key_mappings))

53


In [44]:
def annotate_video(file_path, key_mapping):

    font = cv2.FONT_HERSHEY_SIMPLEX
    bottom_of_screen = (10,400)
    left_of_screen = (10, 200)
    font_scale = 3
    font_color = (255,255,255)
    display_color = (255,0,0)
    line_type = 2
    
    file_name = os.path.basename(file_path)
    cap = cv2.VideoCapture(os.path.join('data/videos', file_name))

    fourcc = cv2.VideoWriter_fourcc(*'XVID')
    fps = cap.get(cv2.CAP_PROP_FPS)
    out = cv2.VideoWriter(os.path.join('data/annotated', file_name),fourcc, fps, (640,480))

    key_timings = key_mapping[0] * fps
    key_strokes = key_mapping[1]

    print(key_strokes)


    frame_num = 0
    last_key = 0
    cur_word = ''
    while(cap.isOpened()):
        ret, frame = cap.read()

        frame_num += 1

        if not ret:
            break

        #gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)

        #frame = cv2.flip(frame,0)
        while frame_num > key_timings[last_key] + 4 and last_key < len(key_strokes) - 1:
            last_key += 1

        if frame_num < key_timings[last_key] + 4 and frame_num > key_timings[last_key] + 2:
            
            key_stroke = key_strokes[last_key].upper()
            cur_word = ''.join(key_strokes[:last_key + 1]).upper()

            if key_stroke == ' ':
                key_stroke = 'space'
            frame = cv2.putText(frame, key_stroke, 
                left_of_screen, 
                font, 
                font_scale,
                display_color,
                line_type)
            
        frame = cv2.putText(frame, cur_word, 
            bottom_of_screen, 
            font, 
            font_scale/2,
            font_color,
            line_type)
            

        #cv2.imshow('frame',frame)

        out.write(frame)


    cap.release()
    out.release()

#cv2.destroyAllWindows()

In [102]:
file_paths = ['videos/0.mp4', 'videos/1.mp4', 'video/2.mp4']
for idx, file in enumerate(file_paths):
    annotate_video(file, key_mappings[idx])

lunatic fringe
lose your marbles
acronyms


In [116]:
print(json.dumps(list(key_mappings[0][0])))

[1.7125, 2.0, 2.2125, 2.475, 2.6875, 2.925, 3.175, 3.8125, 4.3875, 4.6, 4.7875, 5.0375, 5.3625, 5.6125]


In [13]:
with open('data/train.csv', 'w+') as csv_file:
    csv_writer = csv.writer(csv_file, delimiter=',', quotechar='"', quoting=csv.QUOTE_MINIMAL)
    
    for idx, data in enumerate(key_mappings):
        file, time_stamps, label = data 
        file_name = os.path.join('videos/', os.path.basename(file))
        row = [idx, file_name, label, json.dumps(list(time_stamps))]
        csv_writer.writerow(row)

In [45]:
for file_path, time_stamp, label in key_mappings:
    annotate_video(file_path, (time_stamp, label))

lunatic fringe
lose your marbles
acronyms
as cool as a cucumber
a ministering angel shall my sister be
you are what you eat
great balls of fire
make a clean breast of it
we know where you live
clean breast make
jury is still out
pin money
pick n mix
swan song
pond life
one for the road
fast asleep
cut and run
bodice ripper
bugger bognor
tommy atkins
riding shotgun
first dibs
thus far into the bowels of the land
money for old rope
countenance more in sorrow than in anger
my cup of tea
forlorn hope
my bad
throw good money after bad
take potluck
eat my hat
sour grapes
knuckle under
beat swords into ploughshares
technicolor yawn
bite the dust
dogs bollocks
pommy bashing
pound of flesh
lark about
before the fact
lovedup
go to the dogs
sevenyear itch
offing in the
another think coming
moving the goalposts
run of the mill
theres one a sucker born every minute
clue dont have
every cloud has a silver lining
sticky wicket
